# 2.3 从头训练dna bert大模型

In [11]:
import subprocess
import os
# 设置环境变量, autodl一般区域
result = subprocess.run('bash -c "source /etc/network_turbo && env | grep proxy"', shell=True, capture_output=True, text=True)
output = result.stdout
for line in output.splitlines():
    if '=' in line:
        var, value = line.split('=', 1)
        os.environ[var] = value
"""
import os

# 设置环境变量, autodl专区 其他idc
os.environ['HF_ENDPOINT'] = 'https://hf-mirror.com'

# 打印环境变量以确认设置成功
print(os.environ.get('HF_ENDPOINT'))
"""

"\nimport os\n\n# 设置环境变量, autodl专区 其他idc\nos.environ['HF_ENDPOINT'] = 'https://hf-mirror.com'\n\n# 打印环境变量以确认设置成功\nprint(os.environ.get('HF_ENDPOINT'))\n"

In [15]:
from tokenizers import Tokenizer
from tokenizers.models import WordPiece
from tokenizers.trainers import WordPieceTrainer
from tokenizers.pre_tokenizers import Whitespace
from transformers import PreTrainedTokenizerFast,AutoModelForMaskedLM

In [2]:
# 初始化一个空的 WordPiece 模型
tokenizer = Tokenizer(WordPiece(unk_token="[UNK]"))

In [3]:
# 设置训练参数
trainer = WordPieceTrainer(
    vocab_size=30000,        # 词汇表大小
    min_frequency=2,         # 最小词频
    special_tokens=[
        "[PAD]", "[UNK]", "[CLS]", "[SEP]", "[MASK]"
    ]
)

tokenizer.train(files=["../01-data_env/data/dna_1g.txt"], trainer=trainer)

In [4]:
tokenizer.save("dna_wordpiece_dict.json")

## GPT2和bert配置的关键区别
* 最大长度：
在 GPT-2 中，n_ctx 参数指定了模型的最大上下文窗口大小。
在 BERT 中，你应该设置 max_position_embeddings 来指定最大位置嵌入数，这限制了输入序列的最大长度。
* 特殊 token ID：
GPT-2 使用 bos_token_id 和 eos_token_id 分别表示句子的开始和结束。
BERT 使用 [CLS] (cls_token_id) 表示句子的开始，用 [SEP] (sep_token_id) 表示句子的结束。BERT 还有专门的填充 token [PAD] (pad_token_id)。
* 模型类选择：
对于 GPT-2，你使用了 GPT2LMHeadModel，它适合生成任务或语言建模。
对于 BERT，如果你打算进行预训练（例如 Masked Language Modeling），应该使用 BertForMaskedLM。
* 预训练权重：
如果你想从头开始训练，像上面的例子中那样直接从配置创建模型即可。
如果你希望基于现有预训练模型微调，则可以使用 from_pretrained 方法加载预训练权重。

In [7]:
new_tokenizer = Tokenizer.from_file("dna_wordpiece_dict.json")

wrapped_tokenizer = PreTrainedTokenizerFast(
    tokenizer_object=new_tokenizer,
    unk_token="[UNK]",
    pad_token="[PAD]",
    cls_token="[CLS]",
    sep_token="[SEP]",
    mask_token="[MASK]",
)
wrapped_tokenizer.save_pretrained("dna_wordpiece_dict")

('dna_wordpiece_dict/tokenizer_config.json',
 'dna_wordpiece_dict/special_tokens_map.json',
 'dna_wordpiece_dict/tokenizer.json')

In [12]:
from transformers import AutoTokenizer, GPT2LMHeadModel, AutoConfig,GPT2Tokenizer
from transformers import GPT2Tokenizer,GPT2Model,AutoModel
from transformers import DataCollatorForLanguageModeling
from transformers import Trainer, TrainingArguments
from transformers import LineByLineTextDataset
from tokenizers import Tokenizer
from datasets import load_dataset
from transformers import BertConfig, BertModel

In [13]:
tokenizer = AutoTokenizer.from_pretrained("dna_wordpiece_dict")
#tokenizer.pad_token = tokenizer.eos_token

In [16]:
max_length = 256 #最大输入长度

# Building the config
#config = BertConfig()


# 构建配置
config = AutoConfig.from_pretrained(
    "bert-base-uncased",  # 或者其他预训练 BERT 模型名称，这里只是为了获取默认配置
    vocab_size=len(tokenizer),
    max_position_embeddings=max_length,  # 对应于最大位置嵌入数
    pad_token_id=tokenizer.pad_token_id,
    bos_token_id=tokenizer.cls_token_id,  # BERT 使用 [CLS] 作为句子开始标记
    eos_token_id=tokenizer.sep_token_id   # BERT 使用 [SEP] 作为句子结束标记
)


# Building the model from the config
model = AutoModelForMaskedLM.from_config(config)

BertForMaskedLM has generative capabilities, as `prepare_inputs_for_generation` is explicitly overwritten. However, it doesn't directly inherit from `GenerationMixin`. From 👉v4.50👈 onwards, `PreTrainedModel` will NOT inherit from `GenerationMixin`, and this model will lose the ability to call `generate` and other related functions.
  - If you're using `trust_remote_code=True`, you can get rid of this warning by loading the model with an auto class. See https://huggingface.co/docs/transformers/en/model_doc/auto#auto-classes
  - If you are the owner of the model architecture code, please modify your model class such that it inherits from `GenerationMixin` (after `PreTrainedModel`, otherwise you'll get an exception).
  - If you are not the owner of the model architecture class, please contact the model code owner to update it.


In [17]:
# 1. load dna dataset
raw_dataset = load_dataset('text',  data_files="../01-data_env/data/dna_1g.txt")
dataset = raw_dataset["train"].train_test_split(test_size=0.1, shuffle=True)

# 2. tokenize
def tokenize_function(examples):
    return tokenizer(examples['text'], truncation=True, padding='max_length', max_length=max_length)

# 3. 对数据集应用分词函数
tokenized_datasets = dataset.map(tokenize_function, batched=True, remove_columns=['text'], num_proc=15)  # 设置为你的 CPU 核心数或根据需要调整

# 4. 创建一个数据收集器，用于动态填充和遮蔽,注意mlm=true
data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer, mlm=True,mlm_probability=0.15
)

Map (num_proc=15):   0%|          | 0/971635 [00:00<?, ? examples/s]

Map (num_proc=15):   0%|          | 0/107960 [00:00<?, ? examples/s]

In [18]:
run_path = "bert_run"
train_epoches = 5
batch_size = 10


training_args = TrainingArguments(
        output_dir=run_path,
        overwrite_output_dir=True,
        num_train_epochs=train_epoches,
        per_device_train_batch_size=batch_size,
        save_steps=2000,
        save_total_limit=2,
        prediction_loss_only=True,
        fp16=True, #v100没法用
    )


trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["test"],
    data_collator=data_collator,
)

[2024-12-25 22:08:21,898] [INFO] [real_accelerator.py:222:get_accelerator] Setting ds_accelerator to cuda (auto detect)


/root/miniconda3/compiler_compat/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status
/root/miniconda3/compiler_compat/ld: warning: libpthread.so.0, needed by /usr/local/cuda/lib64/libcufile.so, not found (try using -rpath or -rpath-link)
/root/miniconda3/compiler_compat/ld: warning: libstdc++.so.6, needed by /usr/local/cuda/lib64/libcufile.so, not found (try using -rpath or -rpath-link)
/root/miniconda3/compiler_compat/ld: warning: libm.so.6, needed by /usr/local/cuda/lib64/libcufile.so, not found (try using -rpath or -rpath-link)
/root/miniconda3/compiler_compat/ld: /usr/local/cuda/lib64/libcufile.so: undefined reference to `std::runtime_error::~runtime_error()@GLIBCXX_3.4'
/root/miniconda3/compiler_compat/ld: /usr/local/cuda/lib64/libcufile.so: undefined reference to `__gxx_personality_v0@CXXABI_1.3'
/root/miniconda3/compiler_compat/ld: /usr/local/cuda/lib64/libcufile.so: undefined reference to `std::ostream::tellp()@GLIBCXX_3.4'
/root/minicond

In [19]:
trainer.train()
trainer.save_model("dna_bert_v0")

In [ ]:
eval_results = trainer.evaluate()
print(f"Perplexity: {math.exp(eval_results['eval_loss']):.2f}")

In [ ]:
#upload model
#model.push_to_hub("dna_bert_v0", organization="dnagpt", use_auth_token="hf_*******")